In [15]:
import pandas as pd
import sys

from termcolor import cprint

In [16]:
sys.path.append('src/')

import plot as p
from preprocess import DataPreprocessor

pd.set_option('display.max_rows', 1000)
pd.set_option('display.max_columns', 500)

In [17]:
# Load data 
df = pd.read_csv('training_data/kc_house_data.csv') 

In [18]:
 # dropping duplicate rows keeping latest ones
df.sort_values(['id', 'price']).drop_duplicates(subset = 'id', keep = 'last', inplace = True)

## Data preprocessing and feature engineering

In [5]:
# Let's look at the features
df.columns

Index(['id', 'date', 'price', 'bedrooms', 'bathrooms', 'sqft_living',
       'sqft_lot', 'floors', 'waterfront', 'view', 'condition', 'grade',
       'sqft_above', 'sqft_basement', 'yr_built', 'yr_renovated', 'zipcode',
       'lat', 'long', 'sqft_living15', 'sqft_lot15'],
      dtype='object')

#### We would remove id and date column considering both do not contribute towards making predictions

In [19]:
# list to store column names to filter
cols_to_filter = ['id']

#### Let's explore if the sqft_living feature = sqft_above + sqft_basement.

In [20]:
print((df['sqft_above'] + df['sqft_basement'] == df['sqft_living']).all())

True


#### Since sqft_living is the total living area of the house we could drop sqft_basement and sqft_above and only keep sqft_living for representation.

#### Preprocessing --------

   - <font color='blue'>Removing 'id', 'sqft_above', 'sqft_basement.</font>  
   - <font color='blue'>Strip `year` and `month` from date column and removing the date column since it wouldn't help to                generate predictions<br> for new houses on the market.</font>  

#### Feature Generation ------

   - <font color='blue'>yr_built & yr_renovated doesn't seem to have good correlation with price. Let's try a new column, `age` of the house by<br> the time of sale and then `bin` the dates.</font> 
   
   - <font color='blue'>yr_renovated also doesn't seem to have good correlation with price. Let's try a new column, `is_remodel` as to whether or not<br>there was remodelling done to the house.</font> 
   
   - <font color='blue'>We plan to drop sqft_basement considering sqft_living is a good representation but let's try a new column, `has_basement` as to<br> whether or not there is a basement.</font> 
   
   - <font color='blue'>Zipcode in itself as a feature doesn't seem valuable. Curious to experiment if `num_houses_sold_in_zip_code` could have<br> any importance on predictability of price, i.e, how popular an area is.</font> 
   
   - <font color='blue'>Also let's experiment with a feature for `avg_house_size_in_zip_code`.</font> 
   
   - <font color='blue'>lat and long of the house in itself as a feature may not contribute a lot but curious to experiment if `km_dist_from_downtown`<br> could have any importance on predictability of price, i.e, how close a house is from downtown.</font> 
   
   - <font color='blue'>Lastly, experimenting with a new feature for ratio of `sqft_living/sqft_living15` & ratio of `sqft_lot/sqft_lot15`.</font> 


In [21]:
cols_to_filter.extend(['sqft_above', 'sqft_basement'])
cols_to_filter

['id', 'sqft_above', 'sqft_basement']

In [22]:
# DataPreprocessor class to preprocess & generate features

data_prep = DataPreprocessor(datecols = ['date'], cols_to_filter=cols_to_filter)
df = data_prep.fit_transform(df)

In [23]:
# transformed df shape
df.shape

(21613, 27)

In [24]:
# transformed df columns
df.columns

Index(['price', 'bedrooms', 'bathrooms', 'sqft_living', 'sqft_lot', 'floors',
       'waterfront', 'view', 'condition', 'grade', 'sale_year', 'sale_month',
       'age_binned_<1', 'age_binned_1-5', 'age_binned_6-10',
       'age_binned_11-25', 'age_binned_26-50', 'age_binned_51-75',
       'age_binned_76-100', 'age_binned_>100', 'is_renovated', 'has_basement',
       'num_houses_sold_in_zip_code', 'avg_house_size_in_zip_code',
       'km_dist_from_downtown', 'ratio_sqft_living_by_neighbours',
       'ratio_sqft_lot_by_neighbours'],
      dtype='object')

In [28]:
# new features

df[['is_renovated', 'has_basement', 'num_houses_sold_in_zip_code', 'avg_house_size_in_zip_code',
    'km_dist_from_downtown', 'ratio_sqft_living_by_neighbours']].head()

is_renovated  has_basement  num_houses_sold_in_zip_code  \
0             0             0                          262   
1             1             1                          410   
2             0             0                          283   
3             0             1                          263   
4             0             0                          441   

   avg_house_size_in_zip_code  km_dist_from_downtown  \
0                 1729.351145              13.996982   
1                 1745.507317              11.403324   
2                 2122.724382              15.704751   
3                 1726.828897              11.562235   
4                 2645.870748              22.879028   

   ratio_sqft_living_by_neighbours  
0                         0.880597  
1                         1.520710  
2                         0.283088  
3                         1.441176  
4                         0.933333

## Let's look at the new features vs price

In [29]:
for col in ['is_renovated', 'has_basement', 'num_houses_sold_in_zip_code', 'avg_house_size_in_zip_code',
            'km_dist_from_downtown',]:
    
    p.generate_scatter_plot(
        df,
        col,
        'price'
    )